In [ ]:
from sklearn.model_selection import train_test_split
from keras.callbacks import EarlyStopping, ModelCheckpoint
import pandas as pd
import numpy as np
from keras.models import Model
from keras.layers import Input, LSTM, Dense, Bidirectional, Concatenate
from keras.callbacks import EarlyStopping
from keras.layers import Embedding, Attention
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
import matplotlib.pyplot as plt
import nltk
from keras.regularizers import l2
import json

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
data = pd.read_csv('/content/drive/MyDrive/en-ml-names/training_data.csv')

In [ ]:
# # Load the dataset
# f_data = pd.read_csv('/content/drive/MyDrive/en-ml-names-pairs.tsv', sep='\t')
# #data = pd.read_csv('/content/drive/MyDrive/en-ml-names-pairs.tsv', sep='\t')
# # Select the first N rows
# N = 500000
# data = f_data.head(N).copy()

In [ ]:
data

ml             en
0                മോഹനൻ          Mohan
1                   ഉഷ           Usha
2                  ലീല          Leela
3           രേഷ്മ അനിൽ    Reshma Anil
4        അശ്വിൻ തോമസ്  Ashwin Thomas
...                ...            ...
449995          സേവ്യർ         Xavier
449996           സെലിൻ         Celine
449997            ജൂഡി          Joodi
449998            ജെസി          Jessy
449999  അഖിൽരാജ് കെ ജെ  Akhil Raj K J

[450000 rows x 2 columns]

In [ ]:
# Assuming 'ml' is the column containing Malayalam names and 'en' is the English names column in your dataset
malayalam_names = data['ml'].tolist()  # Replace 'data' with the actual variable containing your dataset
english_names = data['en'].tolist()

# Define a function to check if a name contains mostly English characters
def is_english_name(name):
    english_char_count = sum(c.isalpha() and c.isascii() for c in name)
    return english_char_count / len(name) > 0.5  # Adjust the threshold as needed

# Find and count names that are likely to be English in 'ml' column
english_names_ml_column = [name for name in malayalam_names if is_english_name(name)]
count_english_names_ml_column = len(english_names_ml_column)

# Find Malayalam words in the 'en' column
malayalam_words_en_column = [word for word in english_names if not any(c.isascii() for c in word)]
count_malayalam_words_en_column = len(malayalam_words_en_column)

# Print the results
print("Count of English-like Names in Malayalam Names Column:", count_english_names_ml_column)
print("English-like Names in Malayalam Names Column:", english_names_ml_column)

print("\nCount of Malayalam Words in English Names Column:", count_malayalam_words_en_column)
print("Malayalam Words in English Names Column:", malayalam_words_en_column)


Count of English-like Names in Malayalam Names Column: 333
English-like Names in Malayalam Names Column: ['ELIZABETH JOSEPH', 'റെജി THOMAS', 'അനില NARAYANAN', 'ATHIRA KISHORE', 'Jabitha p k', 'LISSEL PAUL', 'Rajeev s', 'Febin Jolly', 'ANNIE CHERIYAN', 'JAYAN', 'NAYANA DILEEP', 'SURENDRAN P P', 'Joseph Antony', 'safna jaffar', 'AGNES ROZARIO', 'Antony K എ ', 'G Vaidhyanathan', 'VARSHA VENKIT', 'ABHISHEK P JAYAN', 'Abhaya Chandran', 'Sharath Anilkumar', 'sakeer thammanam', 'Saumya  Rajkumar', 'AUGUSTINE THANKACHAN', 'Siju P A', 'LISHY SARJITH', 'RIJO REJI', 'T Vijayamma', 'MARY JUDSON', 'raju P S', 'ഗീത Rajesh', 'PUSHPAN K K', 'Rani  Sabu', 'G Vigneshwaran', 'SAJEEV KUMAR V R', 'Deepa. P. S', 'Mr. Kabir Pasha B', 'SHANA NAZRIN M N', 'RANNI.M', 'NADEER FAIZAL', 'Riteshkumar singh', 'THANEESHMA C H', 'NEVIN ANTONY', 'THANKAPPAN', 'Bindhu V S', 'Peter Paul', 'sudheer k gopalan', 'HANI MANOJ', 'Kamarudheen O.A', 'KALLYANIKUTTY AMMA', 'ബീന ROZARIO', 'NIMNA NISHANTH', 'ASHLEN JOSEPH', 'sheeja 

In [ ]:
# Identify English-like names and remove them
english_names_mask = data['ml'].isin(english_names_ml_column)
data = data[~english_names_mask]

# Identify Malayalam words and remove them
malayalam_words_mask = data['en'].isin(malayalam_words_en_column)
data = data[~malayalam_words_mask]

# Remove empty rows
data = data[(data['ml'] != '') & (data['en'] != '')]

# Verify the changes
print("Updated 'ml' column after removing English-like Names:")
print(data['ml'])

print("\nUpdated 'en' column after removing Malayalam Words:")
print(data['en'])


Updated 'ml' column after removing English-like Names:
0                  മോഹനൻ
1                     ഉഷ
2                    ലീല
3             രേഷ്മ അനിൽ
4          അശ്വിൻ തോമസ്
               ...      
449995            സേവ്യർ
449996             സെലിൻ
449997              ജൂഡി
449998              ജെസി
449999    അഖിൽരാജ് കെ ജെ
Name: ml, Length: 449666, dtype: object

Updated 'en' column after removing Malayalam Words:
0                 Mohan
1                  Usha
2                 Leela
3           Reshma Anil
4         Ashwin Thomas
              ...      
449995           Xavier
449996           Celine
449997            Joodi
449998            Jessy
449999    Akhil Raj K J
Name: en, Length: 449666, dtype: object


In [ ]:
# Data Preprocessing
max_seq_length = max(data['ml'].apply(len).max(), data['en'].apply(len).max())

print(max_seq_length)


49


In [ ]:
source_texts = data['ml'].astype(str).tolist()
target_texts = data['en'].astype(str).tolist()

In [ ]:
#source_texts

In [ ]:

source_tokenizer = Tokenizer(char_level=True)
source_tokenizer.fit_on_texts(source_texts)
source_sequences = source_tokenizer.texts_to_sequences(source_texts)
X_train = pad_sequences(source_sequences, maxlen=max_seq_length, padding='post')

target_tokenizer = Tokenizer(char_level=True)
target_tokenizer.fit_on_texts(target_texts)
target_sequences = target_tokenizer.texts_to_sequences(target_texts)
y_train = pad_sequences(target_sequences, maxlen=max_seq_length, padding='post')


In [ ]:
import keras.regularizers as regularizers

# Define the model parameters
embedding_dim = 64
hidden_units = 128

# Define the input layer
input_layer = Input(shape=(max_seq_length,))

# Embedding layer
embedding_layer = Embedding(input_dim=len(source_tokenizer.word_index) + 1, output_dim=embedding_dim, input_length=max_seq_length)(input_layer)

# Bidirectional LSTM layer with L2 regularization
bi_lstm_layer = Bidirectional(LSTM(hidden_units, return_sequences=True, kernel_regularizer=regularizers.l2(l2=0.001)))(embedding_layer)

# Attention layer
attention = Attention()([bi_lstm_layer, bi_lstm_layer])

# Concatenate the output of BiLSTM and Attention
concatenated = Concatenate(axis=-1)([bi_lstm_layer, attention])

# Dense layer with L2 regularization
output_layer = Dense(len(target_tokenizer.word_index) + 1, activation='softmax', kernel_regularizer=regularizers.l2(l2=0.001))(concatenated)

# Define the model
model = Model(inputs=input_layer, outputs=output_layer)

model.summary()

Model: "model"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_1 (InputLayer)        [(None, 49)]                 0         []                            
                                                                                                  
 embedding (Embedding)       (None, 49, 64)               7936      ['input_1[0][0]']             
                                                                                                  
 bidirectional (Bidirection  (None, 49, 256)              197632    ['embedding[0][0]']           
 al)                                                                                              
                                                                                                  
 attention (Attention)       (None, 49, 256)              0         ['bidirectional[0][0]',   

In [ ]:
# Compile the model
model.compile(optimizer='adam', loss='sparse_categorical_crossentropy', metrics=['accuracy'])

# Set up EarlyStopping and ModelCheckpoint
early_stopping = EarlyStopping(monitor='val_loss', patience=3, restore_best_weights=True)
#model_checkpoint = ModelCheckpoint('/content/drive/MyDrive/transliteration_new/best_model.h5', monitor='val_loss', save_best_only=True)


In [ ]:
# Train the model
history = model.fit(X_train, y_train, epochs=8, batch_size=64, validation_split=0.1, callbacks=[early_stopping])


Epoch 1/8
6324/6324 [==============================] - 91s 14ms/step - loss: 0.4871 - accuracy: 0.8778 - val_loss: 0.3061 - val_accuracy: 0.9345
Epoch 2/8
6324/6324 [==============================] - 75s 12ms/step - loss: 0.2551 - accuracy: 0.9468 - val_loss: 0.2294 - val_accuracy: 0.9522
Epoch 3/8
6324/6324 [==============================] - 71s 11ms/step - loss: 0.2163 - accuracy: 0.9548 - val_loss: 0.2077 - val_accuracy: 0.9561
Epoch 4/8
6324/6324 [==============================] - 70s 11ms/step - loss: 0.2012 - accuracy: 0.9575 - val_loss: 0.1985 - val_accuracy: 0.9574
Epoch 5/8
6324/6324 [==============================] - 70s 11ms/step - loss: 0.1931 - accuracy: 0.9588 - val_loss: 0.1921 - val_accuracy: 0.9585
Epoch 6/8
6324/6324 [==============================] - 72s 11ms/step - loss: 0.1879 - accuracy: 0.9597 - val_loss: 0.1883 - val_accuracy: 0.9587
Epoch 7/8
6324/6324 [==============================] - 82s 13ms/step - loss: 0.1842 - accuracy: 0.9604 - val_loss: 0.1844 - val_ac

In [ ]:
import os
import json
from keras.models import load_model

# Save the Keras model as .h5 file
model.save("/content/drive/MyDrive/en-ml-names/model")

In [ ]:
# Save tokenizer configurations as JSON files
source_tokenizer_json = source_tokenizer.to_json()
with open('/content/drive/MyDrive/en-ml-names/source_tokenizer.json', 'w') as f:
    json.dump(source_tokenizer_json, f)

target_tokenizer_json = target_tokenizer.to_json()
with open('/content/drive/MyDrive/en-ml-names/target_tokenizer.json', 'w') as f:
    json.dump(target_tokenizer_json, f)

In [ ]:
# Optionally, you can save the history object for visualization later
with open('/content/drive/MyDrive/en-ml-names/history.json', 'w') as f:
    json.dump(history.history, f)

In [ ]:
# Load the model
model = load_model("/content/drive/MyDrive/en-ml-names/model")

In [ ]:
# Load the tokenizer configurations
with open('/content/drive/MyDrive/en-ml-names/source_tokenizer.json', 'r') as f:
    source_tokenizer_config = json.load(f)
with open('/content/drive/MyDrive/en-ml-names/target_tokenizer.json', 'r') as f:
    target_tokenizer_config = json.load(f)

FileNotFoundError: [Errno 2] No such file or directory: '/content/drive/MyDrive/en-ml-names/source_tokenizer.json'

In [ ]:
# Create new tokenizers from the loaded configurations
from keras.preprocessing.text import tokenizer_from_json
source_tokenizer = tokenizer_from_json(source_tokenizer_config)
target_tokenizer = tokenizer_from_json(target_tokenizer_config)


In [ ]:
# Example input text for prediction
input_text = "അമ്മുക്കുട്ടി"

# Preprocess the input text
input_sequence = source_tokenizer.texts_to_sequences([input_text])
input_sequence_padded = pad_sequences(input_sequence, maxlen=max_seq_length, padding='post')

# Generate predictions
predicted_sequence = model.predict(input_sequence_padded)

# Decode the predicted sequence
predicted_text = "".join(target_tokenizer.index_word[i] for i in np.argmax(predicted_sequence, axis=-1)[0] if i != 0)

print("Input Text:", input_text)
print("Predicted Transliteration:", predicted_text)

1/1 [==============================] - 0s 31ms/step
Input Text: അമ്മുക്കുട്ടി
Predicted Transliteration: ammukkktt


In [ ]:
# Take user input for prediction
input_text = input("Enter the Malayalam text for transliteration: ")

# Preprocess the input text
input_sequence = source_tokenizer.texts_to_sequences([input_text])
input_sequence_padded = pad_sequences(input_sequence, maxlen=max_seq_length, padding='post')

# Generate predictions
predicted_sequence = model.predict(input_sequence_padded)

# Decode the predicted sequence
predicted_text = "".join(target_tokenizer.index_word[i] for i in np.argmax(predicted_sequence, axis=-1)[0] if i != 0)

print("Input Text:", input_text)
print("Predicted Transliteration:", predicted_text)


KeyboardInterrupt: Interrupted by user

In [ ]:
# Load the separate testing dataset
test_data = pd.read_csv('/content/drive/MyDrive/test_data/testing_data.csv')

In [ ]:
# Tokenization and Padding for testing
X_test = pad_sequences(source_tokenizer.texts_to_sequences(test_data['ml'].astype(str).tolist()), maxlen=max_seq_length, padding='post')
y_test = pad_sequences(target_tokenizer.texts_to_sequences(test_data['en'].astype(str).tolist()), maxlen=max_seq_length, padding='post')


NameError: name 'source_tokenizer' is not defined

In [ ]:
# Evaluate the loaded model on the test set
test_loss, test_accuracy = model.evaluate(X_test, y_test)
print(f'Test Loss: {test_loss:.4f}, Test Accuracy: {test_accuracy:.4f}')

1563/1563 [==============================] - 11s 6ms/step - loss: 0.1835 - accuracy: 0.9601
Test Loss: 0.1835, Test Accuracy: 0.9601


In [ ]:
!pip install Levenshtein

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 177.4/177.4 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.4/3.4 MB 75.8 MB/s eta 0:00:00


In [ ]:
from tqdm import tqdm
import Levenshtein
import numpy as np
from tensorflow.keras.preprocessing.sequence import pad_sequences

In [ ]:
# Function to convert sequences back to strings
def sequence_to_text(sequence, tokenizer):
    return tokenizer.sequences_to_texts([sequence])[0]


In [ ]:
# Function to calculate CER
def calculate_cer(model, X, y, source_tokenizer, target_tokenizer, num_samples_to_display=5):
    predictions = model.predict(X)
    decoded_predictions = [sequence_to_text(seq, target_tokenizer) for seq in np.argmax(predictions, axis=-1)]
    decoded_ground_truth = [sequence_to_text(seq, target_tokenizer) for seq in y]

    total_cer = 0.0
    num_samples = min(len(X), num_samples_to_display)

    for i in tqdm(range(num_samples), desc="Calculating CER"):
        cer_value = Levenshtein.distance(decoded_ground_truth[i], decoded_predictions[i])
        cer_value /= len(decoded_ground_truth[i])  # Normalize by the length of the ground truth sequence
        total_cer += cer_value

        # Print ground truth, prediction, input sequence, and Malayalam words without leading/trailing spaces
        print(f"Example {i + 1}:")
        predicted_text_without_spaces = "".join(target_tokenizer.index_word[j] for j in np.argmax(predictions[i], axis=-1) if j != 0)
        ground_truth_without_spaces = "".join(target_tokenizer.index_word[j] for j in y[i] if j != 0)
        print(f"Predicted: {predicted_text_without_spaces}")
        print(f"Ground Truth: {ground_truth_without_spaces}")
        print("=" * 30)

    avg_cer = total_cer / num_samples
    return avg_cer

# Calculate CER using the loaded model
cer_test = calculate_cer(loaded_model, X_test, y_test, source_tokenizer, target_tokenizer, num_samples_to_display=len(X_test))
print(f'Test CER: {cer_test:.4f}')

1563/1563 [==============================] - 9s 5ms/step


Calculating CER:   0%|          | 62/50000 [00:00<01:20, 619.00it/s]

Example 1:
Predicted: baby
Ground Truth: baby
Example 2:
Predicted: sharadddeee    p
Ground Truth: sharafdeen k p
Example 3:
Predicted: vimala
Ground Truth: vimala
Example 4:
Predicted: vittaldas
Ground Truth: vittaldas
Example 5:
Predicted: sabna a s
Ground Truth: sabna a s
Example 6:
Predicted: jobos   avier
Ground Truth: jobson xavier
Example 7:
Predicted: biji muraleedharan
Ground Truth: biji muraleedharan
Example 8:
Predicted: deejas
Ground Truth: deejas
Example 9:
Predicted: nijas
Ground Truth: nijas
Example 10:
Predicted: si vjaaa ttthmmmma
Ground Truth: sr.vijaya(ethamma)
Example 11:
Predicted: poul vaaghess
Ground Truth: paul varghese
Example 12:
Predicted: vironi george
Ground Truth: vironi  george
Example 13:
Predicted: aggustine
Ground Truth: augustine
Example 14:
Predicted: rajeev
Ground Truth: rajeev
Example 15:
Predicted: syamala
Ground Truth: syamala
Example 16:
Predicted: bosec   seeastt
Ground Truth: boskko sebasttin
Example 17:
Predicted: prajeesh s.v
Ground Truth: p

Calculating CER:   0%|          | 184/50000 [00:00<01:24, 591.82it/s]

Predicted: ramar
Ground Truth: ramya
Example 125:
Predicted: jyothilakshmi
Ground Truth: jyothilakshmi
Example 126:
Predicted: p    srrenndrr
Ground Truth: p m surendran
Example 127:
Predicted: si..savvvi
Ground Truth: c.s.xavier
Example 128:
Predicted: smitha p
Ground Truth: smitha p
Example 129:
Predicted: saju k v
Ground Truth: saju k.b.
Example 130:
Predicted: jolly alloonsa
Ground Truth: jolly alphonsa
Example 131:
Predicted: sidhii
Ground Truth: sidhik
Example 132:
Predicted: sareenamla   s
Ground Truth: sareenamol  k s
Example 133:
Predicted: macheal
Ground Truth: micheal
Example 134:
Predicted: prmmachandran
Ground Truth: premachandran
Example 135:
Predicted: yahiya p m
Ground Truth: yahiya p m
Example 136:
Predicted: renjith   .
Ground Truth: renjith a.b.
Example 137:
Predicted: sivapriya
Ground Truth: sivapriya
Example 138:
Predicted: vinitha aaaas
Ground Truth: vinitha alex
Example 139:
Predicted: sheeba b a
Ground Truth: sheeba b a
Example 140:
Predicted: visalakshi
Ground 

...


Ground Truth: shaji m varghese
Example 49324:
Predicted: robin
Ground Truth: robin
Example 49325:
Predicted: sebastian
Ground Truth: sebastian
Example 49326:
Predicted: seleena p s
Ground Truth: celena p c
Example 49327:
Predicted: sarojini
Ground Truth: sarojini
Example 49328:
Predicted: lifhi
Ground Truth: lifi
Example 49329:
Predicted: manoj madhu
Ground Truth: manoj madhu
Example 49330:
Predicted: kastiala  kkoi
Ground Truth: kasttala sekyoora
Example 49331:
Predicted: muraleedharan
Ground Truth: muraleedharan
Example 49332:
Predicted: usha
Ground Truth: usha
Example 49333:
Predicted: edin dicooth
Ground Truth: edin d'couthaa
Example 49334:
Predicted: deepthi savier
Ground Truth: deepthy xavier
Example 49335:
Predicted: jebin
Ground Truth: jebin
Example 49336:
Predicted: binthosh
Ground Truth: bindosh
Example 49337:
Predicted: thresiama
Ground Truth: thresiama
Example 49338:
Predicted: sabu
Ground Truth: sabu
Example 49339:
Predicted: janaki
Ground Truth: janaki
Example 49340:
Pre

Calculating CER: 100%|█████████▉| 49883/50000 [01:02<00:00, 666.77it/s]

Example 49624:
Predicted: antony jjnoy
Ground Truth: antony  jinoy
Example 49625:
Predicted: jinson jacob
Ground Truth: jinsan jacob
Example 49626:
Predicted: ramesan
Ground Truth: ramesan
Example 49627:
Predicted: sunilkumaa k a
Ground Truth: sunil kumar k a
Example 49628:
Predicted: jiyesh p llaa
Ground Truth: jeash pillai
Example 49629:
Predicted: leela
Ground Truth: leela
Example 49630:
Predicted: suman
Ground Truth: suman
Example 49631:
Predicted: mariyamma
Ground Truth: mariamma
Example 49632:
Predicted: paulose joon
Ground Truth: poulose john
Example 49633:
Predicted: amritharraa
Ground Truth: amrutha.t.a
Example 49634:
Predicted: rajaumaa
Ground Truth: raj kumar
Example 49635:
Predicted: jose
Ground Truth: jose
Example 49636:
Predicted: ranjith
Ground Truth: renjith
Example 49637:
Predicted: molly
Ground Truth: molly
Example 49638:
Predicted: srrthi....s
Ground Truth: sruthi.p.s.
Example 49639:
Predicted: rathnakararrarhh
Ground Truth: rathnakaraprabhu
Example 49640:
Predicted:

Calculating CER: 100%|██████████| 50000/50000 [01:02<00:00, 798.36it/s]


Ground Truth: muneera
Example 49952:
Predicted: joshy
Ground Truth: joshy
Example 49953:
Predicted: thayib
Ground Truth: thayib
Example 49954:
Predicted: meharunnisa
Ground Truth: meharunnisa
Example 49955:
Predicted: srathi vaasann
Ground Truth: swathy valsan
Example 49956:
Predicted: ralp  villammgomas
Ground Truth: ralf william gomas
Example 49957:
Predicted: ammini
Ground Truth: ammini
Example 49958:
Predicted: sudha
Ground Truth: sudha
Example 49959:
Predicted: jaseela   c
Ground Truth: jaseela c h
Example 49960:
Predicted: antony
Ground Truth: antony
Example 49961:
Predicted: sindhu
Ground Truth: sindhu
Example 49962:
Predicted: aggustine
Ground Truth: augustine
Example 49963:
Predicted: dhanosh  t d
Ground Truth: dhanush t d
Example 49964:
Predicted: radhamani
Ground Truth: radhamani
Example 49965:
Predicted: tairtn
Ground Truth: daittan
Example 49966:
Predicted: ajitha a m
Ground Truth: ajitha a m
Example 49967:
Predicted: geetha k m
Ground Truth: geetha k m
Example 49968:
Pre